
# MDF-based MDO on the Sobieski SSBJ test case


In [ ]:
from __future__ import annotations

from gemseo import configure_logger
from gemseo import create_discipline
from gemseo import create_scenario
from gemseo import generate_n2_plot
from gemseo.problems.sobieski.core.design_space import SobieskiDesignSpace

configure_logger()

## Instantiate the disciplines
First, we instantiate the four disciplines of the use case:
:class:`.SobieskiPropulsion`,
:class:`.SobieskiAerodynamics`,
:class:`.SobieskiMission`
and :class:`.SobieskiStructure`.



In [ ]:
disciplines = create_discipline([
    "SobieskiPropulsion",
    "SobieskiAerodynamics",
    "SobieskiMission",
    "SobieskiStructure",
])

We can quickly access the most relevant information of any discipline (name, inputs,
and outputs) with Python's ``print()`` function. Moreover, we can get the default
input values of a discipline with the attribute :attr:`.MDODiscipline.default_inputs`



In [ ]:
for discipline in disciplines:
    print(discipline)
    print(f"Default inputs: {discipline.default_inputs}")

You may also be interested in plotting the couplings of your disciplines.
A quick way of getting this information is the high-level function
:func:`.generate_n2_plot`. A much more detailed explanation of coupling
visualization is available `here <coupling_visualization>`.



In [ ]:
generate_n2_plot(disciplines, save=False, show=True)

## Build, execute and post-process the scenario
Then, we build the scenario which links the disciplines
with the formulation and the optimization algorithm. Here, we use the
:class:`.MDF` formulation. We tell the scenario to minimize -y_4 instead of
minimizing y_4 (range), which is the default option.

### Instantiate the scenario
During the instantiation of the scenario, we provide some options for the
MDF formulations:



In [ ]:
formulation_options = {
    "tolerance": 1e-14,
    "max_mda_iter": 50,
    "warm_start": True,
    "use_lu_fact": False,
    "linear_solver_tolerance": 1e-14,
}

- ``'warm_start``: warm starts MDA,
- ``'warm_start``: optimize the adjoints resolution by storing
  the Jacobian matrix LU factorization for the multiple RHS
  (objective + constraints). This saves CPU time if you can pay for
  the memory and have the full Jacobians available, not just matrix vector
  products.
- ``'linear_solver_tolerance'``: set the linear solver tolerance,
  idem we need full convergence




In [ ]:
design_space = SobieskiDesignSpace()
design_space

In [ ]:
scenario = create_scenario(
    disciplines,
    "MDF",
    objective_name="y_4",
    design_space=design_space,
    maximize_objective=True,
    **formulation_options,
)

### Set the design constraints



In [ ]:
for c_name in ["g_1", "g_2", "g_3"]:
    scenario.add_constraint(c_name, "ineq")

### XDSMIZE the scenario
Generate the XDSM file on the fly:

- ``log_workflow_status=True`` will log the status of the workflow  in the console,
- ``save_html`` (default ``True``) will generate a self-contained HTML file,
  that can be automatically opened using ``show_html=True``.



In [ ]:
scenario.xdsmize(save_html=False)

### Define the algorithm inputs
We set the maximum number of iterations, the optimizer
and the optimizer options. Algorithm specific options are passed there.
Use the high-level function :func:`.get_algorithm_options_schema`
for more information or read the documentation.

Here ftol_rel option is a stop criteria based on the relative difference
in the objective between two iterates ineq_tolerance the tolerance
determination of the optimum; this is specific to the |g| wrapping and not
in the solver.



In [ ]:
algo_options = {
    "ftol_rel": 1e-10,
    "ineq_tolerance": 2e-3,
    "normalize_design_space": True,
}
scn_inputs = {"max_iter": 15, "algo": "SLSQP", "algo_options": algo_options}

.. seealso::

   We can also generate a backup file for the optimization,
   as well as plots on the fly of the optimization history if option
   ``generate_opt_plot`` is ``True``.
   This slows down a lot the process, here since SSBJ is very light

   .. code::

    scenario.set_optimization_history_backup(file_path="mdf_backup.h5",
                                             each_new_iter=True,
                                             each_store=False, erase=True,
                                             pre_load=False,
                                             generate_opt_plot=True)



### Execute the scenario



In [ ]:
scenario.execute(scn_inputs)

### Save the optimization history
We can save the whole optimization problem and its history for further post
processing:



In [ ]:
scenario.save_optimization_history("mdf_history.h5", file_format="hdf5")

We can also save only calls to functions and design variables history:



In [ ]:
scenario.save_optimization_history("mdf_history.xml", file_format="ggobi")

### Print optimization metrics



In [ ]:
scenario.print_execution_metrics()

## Post-process the results

### Plot the optimization history view



In [ ]:
scenario.post_process("OptHistoryView", save=False, show=True)

### Plot the basic history view



In [ ]:
scenario.post_process(
    "BasicHistory", variable_names=["x_shared"], save=False, show=True
)

### Plot the constraints and objective history



In [ ]:
scenario.post_process("ObjConstrHist", save=False, show=True)

### Plot the constraints history



In [ ]:
scenario.post_process(
    "ConstraintsHistory",
    constraint_names=["g_1", "g_2", "g_3"],
    save=False,
    show=True,
)

### Plot the constraints history using a radar chart



In [ ]:
scenario.post_process(
    "RadarChart",
    constraint_names=["g_1", "g_2", "g_3"],
    save=False,
    show=True,
)

### Plot the quadratic approximation of the objective



In [ ]:
scenario.post_process("QuadApprox", function="-y_4", save=False, show=True)

### Plot the functions using a SOM



In [ ]:
scenario.post_process("SOM", save=False, show=True)

### Plot the scatter matrix of variables of interest



In [ ]:
scenario.post_process(
    "ScatterPlotMatrix",
    variable_names=["-y_4", "g_1"],
    save=False,
    show=True,
    fig_size=(14, 14),
)

### Plot the variables using the parallel coordinates



In [ ]:
scenario.post_process("ParallelCoordinates", save=False, show=True)

### Plot the robustness of the solution



In [ ]:
scenario.post_process("Robustness", save=True, show=True)

### Plot the influence of the design variables



In [ ]:
scenario.post_process("VariableInfluence", fig_size=(14, 14), save=False, show=True)